# Information Retrieval 1#
## Assignment 2: Retrieval models [100 points] ##

In this assignment you will get familiar with basic and advanced information retrieval concepts. You will implement different information retrieval ranking models and evaluate their performance.

We provide you with a Indri index. To query the index, you'll use a Python package ([pyndri](https://github.com/cvangysel/pyndri)) that allows easy access to the underlying document statistics.

For evaluation you'll use the [TREC Eval](https://github.com/usnistgov/trec_eval) utility, provided by the National Institute of Standards and Technology of the United States. TREC Eval is the de facto standard way to compute Information Retrieval measures and is frequently referenced in scientific papers.

This is a **groups-of-three assignment**, the deadline is **Wednesday, January 31st**. Code quality, informative comments and convincing analysis of the results will be considered when grading. Submission should be done through blackboard, questions can be asked on the course [Piazza](piazza.com/university_of_amsterdam/spring2018/52041inr6y/home).

### Technicalities (must-read!) ###

The assignment directory is organized as follows:
   * `./assignment.ipynb` (this file): the description of the assignment.
   * `./index/`: the index we prepared for you.
   * `./ap_88_90/`: directory with ground-truth and evaluation sets:
      * `qrel_test`: test query relevance collection (**test set**).
      * `qrel_validation`: validation query relevance collection (**validation set**).
      * `topics_title`: semicolon-separated file with query identifiers and terms.

You will need the following software packages (tested with Python 3.5 inside [Anaconda](https://conda.io/docs/user-guide/install/index.html)):
   * Python 3.5 and Jupyter
   * Indri + Pyndri (Follow the installation instructions [here](https://github.com/nickvosk/pyndri/blob/master/README.md))
   * gensim [link](https://radimrehurek.com/gensim/install.html)
   * TREC Eval [link](https://github.com/usnistgov/trec_eval)

### TREC Eval primer ###
The TREC Eval utility can be downloaded and compiled as follows:

    git clone https://github.com/usnistgov/trec_eval.git
    cd trec_eval
    make

TREC Eval computes evaluation scores given two files: ground-truth information regarding relevant documents, named *query relevance* or *qrel*, and a ranking of documents for a set of queries, referred to as a *run*. The *qrel* will be supplied by us and should not be changed. For every retrieval model (or combinations thereof) you will generate a run of the top-1000 documents for every query. The format of the *run* file is as follows:

    $query_identifier Q0 $document_identifier $rank_of_document_for_query $query_document_similarity $run_identifier
    
where
   * `$query_identifier` is the unique identifier corresponding to a query (usually this follows a sequential numbering).
   * `Q0` is a legacy field that you can ignore.
   * `$document_identifier` corresponds to the unique identifier of a document (e.g., APXXXXXXX where AP denotes the collection and the Xs correspond to a unique numerical identifier).
   * `$rank_of_document_for_query` denotes the rank of the document for the particular query. This field is ignored by TREC Eval and is only maintained for legacy support. The ranks are computed by TREC Eval itself using the `$query_document_similarity` field (see next). However, it remains good practice to correctly compute this field.
   * `$query_document_similarity` is a score indicating the similarity between query and document where a higher score denotes greater similarity.
   * `$run_identifier` is an identifier of the run. This field is for your own convenience and has no purpose beyond bookkeeping.
   
For example, say we have two queries: `Q1` and `Q2` and we rank three documents (`DOC1`, `DOC2`, `DOC3`). For query `Q1`, we find the following similarity scores `score(Q1, DOC1) = 1.0`, `score(Q1, DOC2) = 0.5`, `score(Q1, DOC3) = 0.75`; and for `Q2`: `score(Q2, DOC1) = -0.1`, `score(Q2, DOC2) = 1.25`, `score(Q1, DOC3) = 0.0`. We can generate run using the following snippet:

In [ ]:
import logging
import sys
import os

def write_run(model_name, data, out_f,
              max_objects_per_query=sys.maxsize,
              skip_sorting=False):
    """
    Write a run to an output file.
    Parameters:
        - model_name: identifier of run.
        - data: dictionary mapping topic_id to object_assesments;
            object_assesments is an iterable (list or tuple) of
            (relevance, object_id) pairs.
            The object_assesments iterable is sorted by decreasing order.
        - out_f: output file stream.
        - max_objects_per_query: cut-off for number of objects per query.
    """
    for subject_id, object_assesments in data.items():
        if not object_assesments:
            logging.warning('Received empty ranking for %s; ignoring.',
                            subject_id)

            continue

        # Probe types, to make sure everything goes alright.
        # assert isinstance(object_assesments[0][0], float) or \
        #     isinstance(object_assesments[0][0], np.float32)
        assert isinstance(object_assesments[0][1], str) or \
            isinstance(object_assesments[0][1], bytes)

        if not skip_sorting:
            object_assesments = sorted(object_assesments, reverse=True)

        if max_objects_per_query < sys.maxsize:
            object_assesments = object_assesments[:max_objects_per_query]

        if isinstance(subject_id, bytes):
            subject_id = subject_id.decode('utf8')

        for rank, (relevance, object_id) in enumerate(object_assesments):
            if isinstance(object_id, bytes):
                object_id = object_id.decode('utf8')

            out_f.write(
                '{subject} Q0 {object} {rank} {relevance} '
                '{model_name}\n'.format(
                    subject=subject_id,
                    object=object_id,
                    rank=rank + 1,
                    relevance=relevance,
                    model_name=model_name))
            
# The following writes the run to standard output.
# In your code, you should write the runs to local
# storage in order to pass them to trec_eval.
write_run(
    model_name='example',
    data={
        'Q1': ((1.0, 'DOC1'), (0.5, 'DOC2'), (0.75, 'DOC3')),
        'Q2': ((-0.1, 'DOC1'), (1.25, 'DOC2'), (0.0, 'DOC3')),
    },
    out_f=sys.stdout,
    max_objects_per_query=1000)

Now, imagine that we know that `DOC1` is relevant and `DOC3` is non-relevant for `Q1`. In addition, for `Q2` we only know of the relevance of `DOC3`. The query relevance file looks like:

    Q1 0 DOC1 1
    Q1 0 DOC3 0
    Q2 0 DOC3 1
    
We store the run and qrel in files `example.run` and `example.qrel` respectively on disk. We can now use TREC Eval to compute evaluation measures. In this example, we're only interested in Mean Average Precision and we'll only show this below for brevity. However, TREC Eval outputs much more information such as NDCG, recall, precision, etc.

    $ trec_eval -m all_trec -q example.qrel example.run | grep -E "^map\s"
    > map                   	Q1	1.0000
    > map                   	Q2	0.5000
    > map                   	all	0.7500
    
Now that we've discussed the output format of rankings and how you can compute evaluation measures from these rankings, we'll now proceed with an overview of the indexing framework you'll use.

### Pyndri primer ###
For this assignment you will use [Pyndri](https://github.com/cvangysel/pyndri) [[1](https://arxiv.org/abs/1701.00749)], a python interface for [Indri](https://www.lemurproject.org/indri.php). We have indexed the document collection and you can query the index using Pyndri. We will start by giving you some examples of what Pyndri can do:

First we read the document collection index with Pyndri:

In [ ]:
import pyndri

index = pyndri.Index('index/')

The loaded index can be used to access a collection of documents in an easy manner. We'll give you some examples to get some idea of what it can do, it is up to you to figure out how to use it for the remainder of the assignment.

First let's look at the number of documents, since Pyndri indexes the documents using incremental identifiers we can simply take the lowest index and the maximum document and consider the difference:

In [ ]:
print("There are %d documents in this collection." % (index.maximum_document() - index.document_base()))

Let's take the first document out of the collection and take a look at it:

In [ ]:
example_document = index.document(index.document_base())
print(example_document)

Here we see a document consists of two things, a string representing the external document identifier and an integer list representing the identifiers of words that make up the document. Pyndri uses integer representations for words or terms, thus a token_id is an integer that represents a word whereas the token is the actual text of the word/term. Every id has a unique token and vice versa with the exception of stop words: words so common that there are uninformative, all of these receive the zero id.

To see what some ids and their matching tokens we take a look at the dictionary of the index:

In [ ]:
token2id, id2token, _ = index.get_dictionary()
print(list(id2token.items())[:15])

Using this dictionary we can see the tokens for the (non-stop) words in our example document:

In [ ]:
print([id2token[word_id] for word_id in example_document[1] if word_id > 0])

The reverse can also be done, say we want to look for news about the "University of Massachusetts", the tokens of that query can be converted to ids using the reverse dictionary:

In [ ]:
query_tokens = index.tokenize("University of Massachusetts")
print("Query by tokens:", query_tokens)
query_id_tokens = [token2id.get(query_token,0) for query_token in query_tokens]
print("Query by ids with stopwords:", query_id_tokens)
query_id_tokens = [word_id for word_id in query_id_tokens if word_id > 0]
print("Query by ids without stopwords:", query_id_tokens)

Naturally we can now match the document and query in the id space, let's see how often a word from the query occurs in our example document:

In [ ]:
matching_words = sum([True for word_id in example_document[1] if word_id in query_id_tokens])
print("Document %s has %d word matches with query: \"%s\"." % (example_document[0], matching_words, ' '.join(query_tokens)))
print("Document %s and query \"%s\" have a %.01f%% overlap." % (example_document[0], ' '.join(query_tokens),matching_words/float(len(example_document[1]))*100))

While this is certainly not everything Pyndri can do, it should give you an idea of how to use it. Please take a look at the [examples](https://github.com/cvangysel/pyndri) as it will help you a lot with this assignment.

**CAUTION**: Avoid printing out the whole index in this Notebook as it will generate a lot of output and is likely to corrupt the Notebook.

### Parsing the query file
You can parse the query file (`ap_88_89/topics_title`) using the following snippet:

In [1]:
import collections
import io
import logging
import sys

def parse_topics(file_or_files,
                 max_topics=sys.maxsize, delimiter=';'):
    assert max_topics >= 0 or max_topics is None

    topics = collections.OrderedDict()

    if not isinstance(file_or_files, list) and \
            not isinstance(file_or_files, tuple):
        if hasattr(file_or_files, '__iter__'):
            file_or_files = list(file_or_files)
        else:
            file_or_files = [file_or_files]

    for f in file_or_files:
        assert isinstance(f, io.IOBase)

        for line in f:
            assert(isinstance(line, str))

            line = line.strip()

            if not line:
                continue

            topic_id, terms = line.split(delimiter, 1)

            if topic_id in topics and (topics[topic_id] != terms):
                    logging.error('Duplicate topic "%s" (%s vs. %s).',
                                  topic_id,
                                  topics[topic_id],
                                  terms)

            topics[topic_id] = terms

            if max_topics > 0 and len(topics) >= max_topics:
                break

    return topics

with open('./ap_88_89/topics_title', 'r') as f_topics:
    print(parse_topics([f_topics]))

OrderedDict([('51', 'Airbus Subsidies'), ('52', 'South African Sanctions'), ('53', 'Leveraged Buyouts'), ('54', 'Satellite Launch Contracts'), ('55', 'Insider Trading'), ('56', 'Prime (Lending) Rate Moves, Predictions'), ('57', 'MCI'), ('58', 'Rail Strikes'), ('59', 'Weather Related Fatalities'), ('60', 'Merit-Pay vs. Seniority'), ('61', 'Israeli Role in Iran-Contra Affair'), ('62', "Military Coups D'etat"), ('63', 'Machine Translation'), ('64', 'Hostage-Taking'), ('65', 'Information Retrieval Systems'), ('66', 'Natural Language Processing'), ('67', 'Politically Motivated Civil Disturbances'), ('68', 'Health Hazards from Fine-Diameter Fibers'), ('69', 'Attempts to Revive the SALT II Treaty'), ('70', 'Surrogate Motherhood'), ('71', 'Border Incursions'), ('72', 'Demographic Shifts in the U.S.'), ('73', 'Demographic Shifts across National Boundaries'), ('74', 'Conflicting Policy'), ('75', 'Automation'), ('76', 'U.S. Constitution - Original Intent'), ('77', 'Poaching'), ('78', 'Greenpeace'

### Task 1: Implement and compare lexical IR methods [35 points] ### 

In this task you will implement a number of lexical methods for IR using the **Pyndri** framework. Then you will evaluate these methods on the dataset we have provided using **TREC Eval**.

Use the **Pyndri** framework to get statistics of the documents (term frequency, document frequency, collection frequency; **you are not allowed to use the query functionality of Pyndri**) and implement the following scoring methods in **Python**:

- [TF-IDF](http://nlp.stanford.edu/IR-book/html/htmledition/tf-idf-weighting-1.html) and 
- [BM25](http://nlp.stanford.edu/IR-book/html/htmledition/okapi-bm25-a-non-binary-model-1.html) with k1=1.2 and b=0.75. **[5 points]**
- Language models ([survey](https://drive.google.com/file/d/0B-zklbckv9CHc0c3b245UW90NE0/view))
    - Jelinek-Mercer (explore different values of 𝛌 in the range [0.1, 0.5, 0.9]). **[5 points]**
    - Dirichlet Prior (explore different values of 𝛍 [500, 1000, 1500]). **[5 points]**
    - Absolute discounting (explore different values of 𝛅 in the range [0.1, 0.5, 0.9]). **[5 points]**
    - [Positional Language Models](http://sifaka.cs.uiuc.edu/~ylv2/pub/sigir09-plm.pdf) define a language model for each position of a document, and score a document based on the scores of its PLMs. The PLM is estimated based on propagated counts of words within a document through a proximity-based density function, which both captures proximity heuristics and achieves an effect of “soft” passage retrieval. Implement the PLM, all five kernels, but only the Best position strategy to score documents. Use 𝛔 equal to 50, and Dirichlet smoothing with 𝛍 optimized on the validation set (decide how to optimize this value yourself and motivate your decision in the report). **[10 points]**
    
Implement the above methods and report evaluation measures (on the test set) using the hyper parameter values you optimized on the validation set (also report the values of the hyper parameters). Use TREC Eval to obtain the results and report on `NDCG@10`, Mean Average Precision (`MAP@1000`), `Precision@5` and `Recall@1000`.

For the language models, create plots showing `NDCG@10` with varying values of the parameters. You can do this by chaining small scripts using shell scripting (preferred) or execute trec_eval using Python's `subprocess`.

Compute significance of the results using a [two-tailed paired Student t-test](https://docs.scipy.org/doc/scipy/reference/generated/scipy.stats.ttest_rel.html) **[5 points]**. Be wary of false rejection of the null hypothesis caused by the [multiple comparisons problem](https://en.wikipedia.org/wiki/Multiple_comparisons_problem). There are multiple ways to mitigate this problem and it is up to you to choose one.

Analyse the results by identifying specific queries where different methods succeed or fail and discuss possible reasons that cause these differences. This is *very important* in order to understand who the different retrieval functions behave.

**NOTE**: Don’t forget to use log computations in your calculations to avoid underflows. 

**IMPORTANT**: You should structure your code around the helper functions we provide below.

In [ ]:
import time
start_time = time.time()

with open('./ap_88_89/topics_title', 'r') as f_topics:
    queries = parse_topics([f_topics])

index = pyndri.Index('index/')

num_documents = index.maximum_document() - index.document_base()

dictionary = pyndri.extract_dictionary(index)

tokenized_queries = {
    query_id: [dictionary.translate_token(token)
               for token in index.tokenize(query_string)
               if dictionary.has_token(token)]
    for query_id, query_string in queries.items()}

query_term_ids = set(
    query_term_id
    for query_term_ids in tokenized_queries.values()
    for query_term_id in query_term_ids)

print('Gathering statistics about', len(query_term_ids), 'terms.')

# inverted index creation.

document_lengths = {}
unique_terms_per_document = {}

inverted_index = collections.defaultdict(dict)
collection_frequencies = collections.defaultdict(int)

total_terms = 0

for int_doc_id in range(index.document_base(), index.maximum_document()):
    ext_doc_id, doc_token_ids = index.document(int_doc_id)

    document_bow = collections.Counter(
        token_id for token_id in doc_token_ids
        if token_id > 0)
    document_length = sum(document_bow.values())

    document_lengths[int_doc_id] = document_length
    total_terms += document_length

    unique_terms_per_document[int_doc_id] = len(document_bow)

    for query_term_id in query_term_ids:
        assert query_term_id is not None

        document_term_frequency = document_bow.get(query_term_id, 0)

        if document_term_frequency == 0:
            continue

        collection_frequencies[query_term_id] += document_term_frequency
        inverted_index[query_term_id][int_doc_id] = document_term_frequency

avg_doc_length = total_terms / num_documents

print('Inverted index creation took', time.time() - start_time, 'seconds.')

In [ ]:
def run_retrieval(model_name, score_fn):
    """
    Runs a retrieval method for all the queries and writes the TREC-friendly results in a file.
    
    :param model_name: the name of the model (a string)
    :param score_fn: the scoring function (a function - see below for an example) 
    """
    run_out_path = '{}.run'.format(model_name)

    if os.path.exists(run_out_path):
        return

    retrieval_start_time = time.time()

    print('Retrieving using', model_name)

    data = {}

    # TODO: fill the data dictionary. 
    # The dictionary data should have the form: query_id --> (document_score, external_doc_id)
    
    with open(run_out_path, 'w') as f_out:
        write_run(
            model_name=model_name,
            data=data,
            out_f=f_out,
            max_objects_per_query=1000)

In [ ]:
def tfidf(int_document_id, query_term_id, document_term_freq):
    """
    Scoring function for a document and a query term
    
    :param int_document_id: the document id
    :param query_token_id: the query term id (assuming you have split the query to tokens)
    :param document_term_freq: the document term frequency of the query term 
    """
    # TODO implement the function
    score = 0
    return score

# combining the two functions above: 
run_retrieval('tfidf', tfidf)

# TODO implement the rest of the retrieval functions 

# TODO implement tools to help you with the analysis of the results.

### Task 2: Latent Semantic Models (LSMs) [15 points] ###

In this task you will experiment with applying distributional semantics methods ([LSI](http://lsa3.colorado.edu/papers/JASIS.lsi.90.pdf) **[5 points]** and [LDA](https://www.cs.princeton.edu/~blei/papers/BleiNgJordan2003.pdf) **[5 points]**) for retrieval.

You do not need to implement LSI or LDA on your own. Instead, you can use [gensim](http://radimrehurek.com/gensim/index.html). An example on how to integrate Pyndri with Gensim for word2vec can be found [here](https://github.com/cvangysel/pyndri/blob/master/examples/word2vec.py). For the remaining latent vector space models, you will need to implement connector classes (such as `IndriSentences`) by yourself.

In order to use a latent semantic model for retrieval, you need to:
   * build a representation of the query **q**,
   * build a representation of the document **d**,
   * calculate the similarity between **q** and **d** (e.g., cosine similarity, KL-divergence).
     
The exact implementation here depends on the latent semantic model you are using. 
   
Each of these LSMs come with various hyperparameters to tune. Make a choice on the parameters, and explicitly mention the reasons that led you to these decisions. You can use the validation set to optimize hyper parameters you see fit; motivate your decisions. In addition, mention clearly how the query/document representations were constructed for each LSM and explain your choices.

In this experiment, you will first obtain an initial top-1000 ranking for each query using TF-IDF in **Task 1**, and then re-rank the documents using the LSMs. Use TREC Eval to obtain the results and report on `NDCG@10`, Mean Average Precision (`MAP@1000`), `Precision@5` and `Recall@1000`.

Perform significance testing **[5 points]** (similar as in Task 1) in the class of semantic matching methods.

In [3]:
import gensim
import pyndri
import collections

# taken from http://www.pythonexample.com/code/gensim-python-tutorial/

class LDALSISentences(gensim.interfaces.CorpusABC):
 
    def __init__(self, index, dictionary, max_documents=None):
        assert isinstance(index, pyndri.Index)
 
        self.index = index
        self.dictionary = dictionary
 
        self.max_documents = max_documents
 
    def _maximum_document(self):
        if self.max_documents is None:
            return self.index.maximum_document()
        else:
            return min(
                self.max_documents + self.index.document_base(),
                self.index.maximum_document())
 
    def _doc2bow(self, doc):
 
        di = collections.defaultdict(int)
         
        for token_id in doc:
            di[token_id] += 1
 
        return [(key, value) for key, value in di.items()]
 
    def __iter__(self):
        for int_doc_id in range(self.index.document_base(),
                                self._maximum_document()):
            ext_doc_id, tokens = self.index.document(int_doc_id)
 
            tokens = tuple(
                token_id
                for token_id in tokens
                if token_id > 0 and token_id in self.dictionary)
 
            yield self._doc2bow(tokens)
 
    def __len__(self):
        return self._maximum_document() - self.index.document_base()

In [4]:
import pyndri
index = pyndri.Index('index/')

external2int = {}
for int_doc_id in range(index.document_base(), index.maximum_document()):
    ext_doc_id, _ = index.document(int_doc_id)
    external2int[ext_doc_id] = int_doc_id

In [7]:
from scipy.stats import entropy

def prob_distr(lda_vec1, lda_vec2, num_topics, measure_type):
    dense_lda_vec1 = gensim.matutils.sparse2full(lda_vec1, num_topics)
    dense_lda_vec2 = gensim.matutils.sparse2full(lda_vec2, num_topics)
    #print out sums of distributions: mst be equal to 1
    if measure_type == "hellinger_distance":
        return np.sqrt(np.sum((np.sqrt(dense_lda_vec1) - np.sqrt(dense_lda_vec2)) ** 2)) / np.sqrt(2)
    elif measure_type == "KL_divergence":
        return np.sum(np.where(dense_lda_vec1 != 0, dense_lda_vec1 * np.log(dense_lda_vec1 / dense_lda_vec2), 0))
        #return entropy(dense_lda_vec1, dense_lda_vec2) 
        # to add an extension for symmetric KL?

In [5]:
import copy
import pyndri
import pyndri.compat
import sys
import time
import numpy as np
import itertools
import logging
from collections import Counter
from gensim import corpora, models, similarities


start_time = time.time()
print('{:.1f}s: Loading pyndri index'.format(time.time() - start_time))
index = pyndri.Index('index/')
dictionary = pyndri.extract_dictionary(index)

token2id, id2token, _ = index.get_dictionary()

print('{:.1f}s: Loading queries'.format(time.time() - start_time))
with open('./ap_88_89/topics_title', 'r') as f_topics:
    queries = parse_topics([f_topics])
tokenized_queries = {
    query_id: [dictionary.translate_token(token)
               for token in index.tokenize(query_string)
               if dictionary.has_token(token)]
    for query_id, query_string in queries.items()}
query_term_ids = set(
    query_term_id
    for query_term_ids in tokenized_queries.values()
    for query_term_id in query_term_ids)

print('{:.1f}s: Convert index to IndriSentences (streaming corpus)'.format(time.time() - start_time))
#sentences = pyndri.compat.IndriSentences(index, dictionary)
sentences = LDALSISentences(index, dictionary)

#print('{:.1f}s: Constructing LSI model'.format(time.time() - start_time))
#lsi = models.lsimodel.LsiModel(corpus=sentences, id2word=dictionary.id2token, num_topics=10, \
#                               chunksize=20000, decay=1.0, distributed=False, onepass=True, \
#                               power_iters=2, extra_samples=100)    
#lsi.save('10topics.lsi')
#print('{:.1f}s: LSI constructed successfully'.format(time.time() - start_time))

print('{:.1f}s: Constructing LDA model'.format(time.time() - start_time))
number_of_topics = 25

fname_log = 'LDA'+str(number_of_topics)+'topics.log'
fname_model = 'LDA'+str(number_of_topics)+'topics.model'

logging.basicConfig(filename=fname_log, level=logging.INFO)
logging.root.level = logging.INFO

lda = models.ldamodel.LdaModel(corpus=sentences, num_topics=number_of_topics, id2word=id2token, distributed=False, \
                               chunksize=2000, update_every=1, passes=1, alpha='symmetric', \
                               eta=None, decay=0.5, offset=1.0, eval_every=10, iterations=50, \
                               gamma_threshold=0.001, minimum_probability=0.01, random_state=None, \
                               ns_conf=None, minimum_phi_value=0.01, per_word_topics=False, \
                               callbacks=None)
lda.save(fname_model)
print('{:.1f}s: LDA constructed successfully'.format(time.time() - start_time))

0.0s: Loading pyndri index
3.0s: Loading queries


INFO:gensim.models.ldamodel:using symmetric alpha at 0.3333333333333333
INFO:gensim.models.ldamodel:using serial LDA version on this node


3.6s: Convert index to IndriSentences (streaming corpus)
3.6s: Constructing LDA model


INFO:gensim.models.ldamodel:running online (single-pass) LDA training, 3 topics, 1 passes over the supplied corpus of 164597 documents, updating model once every 2000 documents, evaluating perplexity every 20000 documents, iterating 50x with a convergence threshold of 0.001000
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #2000/164597
INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"new" + 0.004*"1" + 0.003*"000" + 0.003*"people" + 0.003*"two" + 0.003*"years" + 0.003*"president" + 0.003*"bush" + 0.003*"government" + 0.002*"percent"
INFO:gensim.models.ldamodel:topic #1 (0.333): 0.004*"new" + 0.004*"million" + 0.004*"government" + 0.004*"two" + 0.004*"1" + 0.003*"people" + 0.003*"tuesday" + 0.002*"police" + 0.002*"2" + 0.002*"three"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.005*"percent" + 0.004*"million" + 0.004*"new" + 0.003*"president" + 0.003*"people" + 0.003*"two" +

INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.005*"president" + 0.005*"soviet" + 0.004*"people" + 0.004*"new" + 0.004*"party" + 0.003*"two" + 0.003*"bush" + 0.003*"united" + 0.003*"years"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.011*"percent" + 0.009*"million" + 0.008*"1" + 0.006*"new" + 0.005*"2" + 0.005*"billion" + 0.004*"5" + 0.004*"company" + 0.004*"3" + 0.004*"market"
INFO:gensim.models.ldamodel:topic diff=0.216215, rho=0.316228
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #22000/164597
INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"two" + 0.004*"court" + 0.004*"people" + 0.003*"police" + 0.003*"state" + 0.003*"new" + 0.003*"years" + 0.003*"three" + 0.003*"officials" + 0.003*"000"
INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.005*"soviet" + 0.005*"president" + 0.004*"people" + 0.004*"new" + 0.003*"party" + 0.003*"b

...

INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.006*"president" + 0.005*"soviet" + 0.004*"bush" + 0.004*"people" + 0.004*"party" + 0.004*"united" + 0.004*"two" + 0.003*"states" + 0.003*"military"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.014*"percent" + 0.010*"million" + 0.010*"1" + 0.006*"new" + 0.006*"2" + 0.005*"billion" + 0.005*"5" + 0.004*"company" + 0.004*"3" + 0.004*"market"
INFO:gensim.models.ldamodel:topic diff=0.116397, rho=0.142857
INFO:gensim.models.ldamodel:-8.881 per-word bound, 471.3 perplexity estimate based on a held-out corpus of 2000 documents with 521243 words
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #100000/164597
INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"two" + 0.004*"people" + 0.003*"court" + 0.003*"new" + 0.003*"years" + 0.003*"state" + 0.003*"000" + 0.003*"police" + 0.003*"three" + 0.002*"time"
INFO:gensim.model

INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"two" + 0.004*"people" + 0.003*"new" + 0.003*"years" + 0.003*"court" + 0.003*"000" + 0.003*"police" + 0.003*"state" + 0.003*"three" + 0.002*"time"
INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.006*"president" + 0.005*"soviet" + 0.005*"bush" + 0.004*"people" + 0.004*"united" + 0.004*"two" + 0.004*"party" + 0.004*"states" + 0.003*"dukakis"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.015*"percent" + 0.010*"1" + 0.010*"million" + 0.006*"new" + 0.006*"2" + 0.006*"billion" + 0.005*"5" + 0.004*"company" + 0.004*"3" + 0.004*"market"
INFO:gensim.models.ldamodel:topic diff=0.113170, rho=0.130189
INFO:gensim.models.ldamodel:-8.845 per-word bound, 460.0 perplexity estimate based on a held-out corpus of 2000 documents with 500539 words
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #120000/164597
INFO:gensim.models

INFO:gensim.models.ldamodel:topic #2 (0.333): 0.015*"percent" + 0.011*"1" + 0.010*"million" + 0.006*"new" + 0.006*"2" + 0.005*"billion" + 0.005*"5" + 0.004*"3" + 0.004*"company" + 0.004*"market"
INFO:gensim.models.ldamodel:topic diff=0.104867, rho=0.121268
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #138000/164597
INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"two" + 0.004*"people" + 0.003*"new" + 0.003*"years" + 0.003*"court" + 0.003*"000" + 0.003*"state" + 0.003*"police" + 0.002*"three" + 0.002*"time"
INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"president" + 0.006*"government" + 0.005*"soviet" + 0.005*"bush" + 0.004*"dukakis" + 0.004*"party" + 0.004*"two" + 0.004*"people" + 0.004*"united" + 0.004*"states"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.015*"percent" + 0.010*"1" + 0.010*"million" + 0.006*"new" + 0.006*"2" + 0.005*"billion" + 0.005*"5" + 0.004*"c

INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.006*"president" + 0.005*"soviet" + 0.005*"bush" + 0.005*"dukakis" + 0.004*"two" + 0.004*"people" + 0.004*"party" + 0.004*"united" + 0.004*"states"
INFO:gensim.models.ldamodel:topic #2 (0.333): 0.016*"percent" + 0.010*"million" + 0.010*"1" + 0.006*"new" + 0.006*"2" + 0.005*"billion" + 0.005*"5" + 0.004*"company" + 0.004*"market" + 0.004*"3"
INFO:gensim.models.ldamodel:topic diff=0.095299, rho=0.113228
INFO:gensim.models.ldamodel:PROGRESS: pass 0, at document #158000/164597
INFO:gensim.models.ldamodel:merging changes from 2000 documents into a model of 164597 documents
INFO:gensim.models.ldamodel:topic #0 (0.333): 0.004*"two" + 0.004*"people" + 0.004*"new" + 0.003*"years" + 0.003*"court" + 0.003*"000" + 0.003*"police" + 0.003*"state" + 0.003*"time" + 0.002*"three"
INFO:gensim.models.ldamodel:topic #1 (0.333): 0.006*"government" + 0.006*"president" + 0.005*"soviet" + 0.005*"bush" + 0.005*"dukakis" + 0.004*"two" + 0.004*"

3637.1s: LDA constructed successfully


In [70]:
# LSI

from gensim import corpora, models, similarities
lsi = models.LsiModel.load("./saved_models/lsi500topics.lsi")
print('{:.1f}s: Loading pyndri index'.format(time.time() - start_time))
index = pyndri.Index('index/')
dictionary = pyndri.extract_dictionary(index)
print('{:.1f}s: Loading queries'.format(time.time() - start_time))
with open('./ap_88_89/topics_title', 'r') as f_topics:
    queries = parse_topics([f_topics])

#corpus_lsi = lsi[sentences]
#print('corpus_lsi = ', corpus_lsi)

#print('{:.1f}s: Calculating the similarity matrix'.format(time.time() - start_time))

lsi_file = open("lsi500topics.run", "w")
tfidf_file = open("tfidf.run", "r")
#query_counter = 0
for query_id, query in queries.items():
    print(query_id)
    doc = []
    ext_doc = []
    print('{}: {}'.format(query_id,query))
    for line in range(1000):
        line1 = tfidf_file.readline().split()
        our_ext_doc_id = line1[2]
        our_int_doc_id = external2int[our_ext_doc_id]
        #for int_doc_id, score in results:
        ext_doc_id, doc_token_ids = index.document(our_int_doc_id)
        #print('int_doc_id = {}, score = {} doc_token_ids = {}'.format(int_doc_id, score, doc_token_ids))
        token_id_counts = Counter(token_id for token_id in doc_token_ids if token_id > 0)
        #doc.append([ext_doc_id, list(token_id_counts.items())])
        doc.append(list(token_id_counts.items()))
        ext_doc.append(our_ext_doc_id)
        #print(doc)   
        #print("Document: {}".format(doc[0][1]))  #doc[ext_doc_id][list of token_id_counts]

    print('query = ', query)
    query_bow = dictionary.doc2bow(query.lower().split()) # bow-representation of the query
    print('query_bow = ', query_bow)
    query_lsi = lsi[query_bow] # representation of the input (q_bow) in the latent space
    print('query_lsi = ', query_lsi)
    query_norm = np.linalg.norm(query_lsi)
    #lsi.print_topics(20)

    ind_lsi = similarities.MatrixSimilarity(lsi[doc]) # transform corpus to LSI space and index it
    sims_lsi = ind_lsi[query_lsi] # calculate query-against-corpus (query-against-document?) cosine similarity 
    print('sims_lsi = ',sims_lsi)
  
    print('{:.1f}s: Similarity matrix calculated'.format(time.time() - start_time))
    
    #sort similarity scores
    sorted_sims = [(ext_doc[i], sim_score) for i, sim_score in enumerate(sims_lsi)]
    #print('sorted_sims:\t',sorted_sims)
    corpus_sorted = tuple(sorted(sorted_sims, key=lambda sims_lsi: sims_lsi[1], reverse=True))
    #print('corpus_sorted:\t',corpus_sorted)
    for i, (ext, score) in enumerate(corpus_sorted):
        #print('{} Q0 {} {} {} lsi_cos'.format(query_id,ext,(i+1),score))
        lsi_file.write('{} Q0 {} {} {} lsi_cos\n'.format(query_id,ext,(i+1),score))
    #break

lsi_file.close()
tfidf_file.close()

14473.5s: Loading pyndri index
14494.2s: Loading queries
51
51: Airbus Subsidies
query =  Airbus Subsidies
query_bow =  [(3066, 1), (5872, 1)]
query_lsi =  [(0, -0.004357459359684814), (1, -0.000686475224234254), (2, 0.00011057176451732065), (3, 0.001113053844837134), (4, -0.002153085772513119), (5, -0.00026722107964768693), (6, -0.007976593218957974), (7, -0.004231157539470831), (8, -0.0039742355954009104), (9, -0.0016910427827763136), (10, 0.001895920346554025), (11, 0.0004608517914553383), (12, -0.0018741919611577845), (13, 0.004818441353493576), (14, 0.006163944347885265), (15, 0.003023838070622676), (16, 0.004158492807074935), (17, 0.0040367071894915505), (18, -0.0014831416724225216), (19, -0.0019893747851280476), (20, 0.0018552128376454295), (21, -0.00533232355509913), (22, -0.007432083122916293), (23, -0.0027885864340619123), (24, -0.0096585087303389), (25, -0.00442613273145403), (26, -0.0022288100959428313), (27, -0.0004418445914659058), (28, 0.0024052577871662355), (29, -0.001

sims_lsi =  [ 0.40363762  0.40837678  0.2113615   0.42099336  0.2743132   0.23466831
  0.35763276  0.21615717  0.1958369   0.16792196  0.2291639   0.18486881
  0.20066646  0.2283239   0.4439222   0.27143434  0.2579382   0.07521828
  0.23573144  0.24139835  0.27597854  0.24637488  0.24484824  0.14471985
  0.28146565  0.27853253  0.44674617  0.38578907  0.27562535  0.19705445
  0.23047036  0.19886373  0.1788472   0.17481904  0.22864069  0.11418815
  0.25800908  0.4882517   0.22484846  0.23093611  0.28476876  0.30579022
  0.3735043   0.24859813  0.22635871  0.21481177  0.15633811  0.23546289
  0.29122764  0.3096658   0.1530664   0.15437512  0.39177534  0.42652506
  0.275889    0.37579963  0.13935776  0.22853625  0.245412    0.21529181
  0.23451273  0.22767028  0.26371825  0.25561017  0.32561055  0.26014492
  0.31419474  0.30008045  0.26022846  0.16896902  0.20643999  0.20836538
  0.30805737  0.3432363   0.41675496  0.4881203   0.37151635  0.20139934
  0.3793193   0.31536737  0.21642083  0

query =  South African Sanctions
query_bow =  [(54, 1), (846, 1), (2208, 1)]
query_lsi =  [(0, -0.060919943815127955), (1, -0.0506088149236648), (2, 0.0034966859275624455), (3, -0.017412891010704645), (4, 0.05785597444103086), (5, -0.05060211427642622), (6, -0.007151033241359479), (7, 0.0320631247029734), (8, 0.06527212645001035), (9, 0.0037146434514848474), (10, -0.003917362822457486), (11, 0.06817073959290043), (12, -0.1587271436401696), (13, -0.00369485506660583), (14, 0.08049358987283771), (15, 0.04669543343010252), (16, 0.03927210316028083), (17, 0.12033128924988), (18, 0.1266432625400496), (19, -0.19040635071259066), (20, -0.010203791769205661), (21, -0.04679164531780044), (22, -0.041803054420253644), (23, -0.00414488981591959), (24, 0.0876240818939134), (25, -0.08921276983488), (26, -0.34890352559991133), (27, 0.35901667625470507), (28, -0.35332038562921925), (29, 0.27041289596533774), (30, -0.06704843807287031), (31, -0.1677732015417798), (32, 0.0885724016013127), (33, -0.38346

sims_lsi =  [0.64928144 0.85564727 0.7409822  0.6742657  0.83934116 0.6780381
 0.6751418  0.76457196 0.7559693  0.7701802  0.78570944 0.7716748
 0.6007487  0.7825296  0.58207715 0.60975444 0.5342382  0.5289557
 0.75594467 0.84608763 0.70106274 0.6101012  0.703017   0.6535128
 0.74915856 0.6129575  0.6216906  0.6631474  0.6971051  0.6191625
 0.72834367 0.7271098  0.84348625 0.79558843 0.7956069  0.63220733
 0.6433803  0.7290998  0.76223356 0.5505738  0.73406166 0.70123255
 0.7749456  0.7878143  0.5688058  0.69110775 0.65768355 0.5612352
 0.7920253  0.75364125 0.6474962  0.54076993 0.69489396 0.7916754
 0.6224538  0.7199133  0.753766   0.73626125 0.79138297 0.72700495
 0.6297646  0.44074768 0.79430765 0.6704402  0.864732   0.66138226
 0.7876352  0.760675   0.6678281  0.7154249  0.75323963 0.5883465
 0.6784639  0.58330995 0.73317313 0.67446935 0.7054371  0.7947275
 0.7637445  0.5974835  0.46350452 0.69923615 0.5269379  0.74745697
 0.7965256  0.80074316 0.41687864 0.66933113 0.74620944 0.7

query =  Leveraged Buyouts
query_bow =  [(4886, 1), (48553, 1)]
query_lsi =  [(0, -0.002393523318383533), (1, 0.0010333959028185622), (2, 0.00023423910225763963), (3, 0.003733886168657256), (4, -0.002426641410100261), (5, 0.0034228257586616006), (6, -0.002390734361178719), (7, -0.0045323730017800415), (8, -0.0044876753195911764), (9, -0.006060591657048595), (10, -0.0037384060793917303), (11, -0.004174424318432637), (12, -0.0016339673361976872), (13, 0.0013882101645391598), (14, 0.005865818488653861), (15, -0.007726661301272418), (16, -0.006484871653529244), (17, -0.003538393403056765), (18, 0.0019934360841610925), (19, 0.0023401605488630167), (20, 0.0011054124867110957), (21, -0.00034674337266047946), (22, -0.0008763018735254643), (23, 0.005274812590842785), (24, -0.004350510319606394), (25, 0.0017037088855234367), (26, -0.006811879821666607), (27, 0.00325548254528122), (28, 0.005025157937137343), (29, -0.0005497375647075065), (30, 0.0007562109984178755), (31, -0.0028677182366304162), 

...

sims_lsi =  [ 0.22445944  0.25621873  0.24396682  0.28058046  0.1882822   0.29381022
  0.29501057  0.36969963  0.28737366  0.23000868  0.28697443  0.26832741
  0.3216075   0.25986284  0.23249187  0.29623613  0.17623529  0.22360982
  0.21115993  0.19036537  0.10873625  0.1919514   0.20164023  0.28699186
  0.3168358   0.14868096  0.16667545  0.22923073  0.26659834  0.18274148
  0.2205293   0.2922366   0.18764718  0.21879162  0.0347843   0.07853949
  0.10437782  0.05209937  0.21651708  0.29817855  0.2976948   0.27097112
  0.24975672  0.213762    0.19774121  0.08958182  0.16296375  0.11592183
  0.05853764  0.23521404  0.15227306  0.23844485  0.1792466   0.2327642
  0.25937957  0.11755707  0.11527116  0.22699651  0.20859678  0.48833793
  0.06811972  0.1481771   0.21084519  0.46241155  0.28250855  0.2157709
  0.26235828  0.22870453  0.16278921  0.16269769  0.28852022  0.27405825
  0.04143752  0.19956706  0.21122487  0.0459269   0.216928    0.4876836
  0.35726044  0.3174775   0.42132628  0.35

query =  Legality of Medically Assisted Suicides
query_bow =  [(29064, 1), (141966, 1), (156066, 1), (231615, 1)]
query_lsi =  [(0, -0.0012234131929126871), (1, -0.0008371292789966859), (2, 7.431295142298531e-05), (3, -7.858327005305345e-05), (4, 0.001037067961488583), (5, 0.0010327730898151918), (6, 0.0005603729796132956), (7, -0.0008640472672538396), (8, -0.0013094432611223629), (9, 0.0003483457698732895), (10, 6.870206650072853e-05), (11, -0.00034402762746368453), (12, 7.534703856503823e-05), (13, 0.0004044599856123208), (14, -0.0012782304683681724), (15, 0.0007987151674221664), (16, 0.00022380711039690298), (17, 0.0002624729290096666), (18, -0.00018683969505852935), (19, -0.0002567100178946574), (20, -0.000254334700471974), (21, 0.00024144205261905595), (22, -0.00020671909468379125), (23, -0.00043193673562133946), (24, 0.00030869959336526307), (25, 0.0009053591524688387), (26, 0.0009121291006463767), (27, -0.00017507735569216901), (28, 0.0001256038005477182), (29, 0.000239913678485

sims_lsi =  [ 1.63508743e-01  1.89308241e-01  2.17981845e-01  1.94051266e-01
  2.46048763e-01  2.53603041e-01  1.19510278e-01  1.60887957e-01
  1.38548657e-01  2.26025149e-01  1.84413269e-01  1.21248387e-01
  2.33705580e-01  2.35846564e-01  2.76178330e-01  1.29440054e-01
  1.48863256e-01  1.67809129e-01  1.59842744e-01  8.19390044e-02
  2.06723884e-01  6.84918985e-02  1.79258227e-01  1.18197724e-01
  2.32605845e-01  1.39043599e-01  3.07335127e-02  2.13277079e-02
  1.40974587e-02  1.50062770e-01  1.94754526e-01  6.76971897e-02
  1.91791311e-01  7.26839751e-02  9.19389650e-02  1.42861545e-01
  1.08456470e-01  1.62852958e-01  1.73810437e-01  1.12628140e-01
  8.94692838e-02  1.98007911e-01  5.74247874e-02  7.19701499e-02
  1.34823754e-01 -1.56891346e-02  5.54562658e-02  7.87492394e-02
  1.83222339e-01  1.20187961e-01  1.09272465e-01  9.92491171e-02
  6.60816506e-02  1.76625133e-01  1.61217943e-01  1.92305133e-01
  1.16906345e-01  1.21826589e-01  1.73934862e-01  1.69174120e-01
  8.47459361e

query =  Impact of foreign textile imports on U.S. textile industry
query_bow =  [(69, 1), (277, 1), (1404, 1), (1783, 1), (238359, 2)]
query_lsi =  [(0, -0.0877190362945541), (1, -0.021064296520056622), (2, 0.0033385222818430476), (3, 0.00403714331820223), (4, -0.014711771899940097), (5, -0.056621907145089564), (6, -0.11812219719021312), (7, -0.04752553507369792), (8, -0.0388739345945124), (9, -0.04201386312851669), (10, -0.02653163284121788), (11, -0.011828951468960793), (12, -0.008989702304324807), (13, 0.037300873937988616), (14, 0.05567886617516113), (15, -0.0044082717727461414), (16, 0.008742699123436273), (17, 0.06106922853249961), (18, -0.004889254565850903), (19, -0.033031248039022694), (20, -0.023820603120004277), (21, -0.0070204250110508775), (22, -0.06855436358847425), (23, -0.015936564002137065), (24, -0.06882321967486904), (25, -0.04087065972202339), (26, -0.04985270933896972), (27, 0.016975051261871675), (28, 0.019365656281125358), (29, -1.1890410207579354e-05), (30, 0.0

sims_lsi =  [ 2.69048870e-01  4.03384745e-01  2.50976324e-01  3.02841663e-01
  1.48710951e-01  3.55118990e-01  3.12193424e-01  1.88022524e-01
  1.77452385e-01  4.07588571e-01  2.67222106e-01  1.64043814e-01
  2.60779768e-01  2.83373535e-01  1.99057460e-01  1.73714206e-01
  2.11902320e-01  2.57205486e-01  2.41922662e-01  2.59913415e-01
  1.76274434e-01  1.70391560e-01  3.14331800e-01  1.20637253e-01
  3.10472399e-01  1.74063891e-01  1.26276687e-01  1.59230500e-01
  1.92610517e-01  1.40105784e-01  1.01096213e-01  1.34965777e-01
  1.05862714e-01  1.39021888e-01  2.39116490e-01  1.02600075e-01
  9.27684158e-02  9.90483835e-02  7.66260326e-02  5.35395108e-02
  6.50813058e-02  7.55474344e-02  4.88147736e-02  2.01464333e-02
  1.60369202e-01  3.83019783e-02  1.58296824e-01  2.45613113e-01
  4.20155257e-01  6.16434477e-02  3.62200588e-02  4.21027280e-02
  9.07033458e-02  6.54784590e-02  1.56539395e-01  5.22770546e-02
  8.25800225e-02  2.33336836e-01  3.91454883e-02  7.23523870e-02
  5.17826304e

In [67]:
# LDA

#lda = models.LdaModel.load("./saved_models/lda200topics.lda")
lda = models.LdaModel.load("10topics.lda")
number_of_topics = 10

lda_file = open("lda10topics.run", "w")
tfidf_file = open("tfidf.run", "r")
#query_counter = 0
for query_id, query in queries.items():
    #print(query_id)
    #if int(query_id) != 53:
    #    continue
    doc = []
    ext_doc = []
    print('{}: {}'.format(query_id,query))
    for line in range(1000):
        line1 = tfidf_file.readline().split()
        our_ext_doc_id = line1[2]
        our_int_doc_id = external2int[our_ext_doc_id]
        #for int_doc_id, score in results:
        ext_doc_id, doc_token_ids = index.document(our_int_doc_id)
        #print('int_doc_id = {}, score = {} doc_token_ids = {}'.format(int_doc_id, score, doc_token_ids))
        token_id_counts = Counter(token_id for token_id in doc_token_ids if token_id > 0)
        #doc.append([ext_doc_id, list(token_id_counts.items())])
        doc.append(list(token_id_counts.items()))
        ext_doc.append(our_ext_doc_id)
        #print(doc)   
        #print("Document: {}".format(doc[0][1]))  #doc[ext_doc_id][list of token_id_counts]

    print('query = ', query)
    query_bow = dictionary.doc2bow(query.lower().split()) # bow-representation of the query
    print('query_bow = ', query_bow)
    query_lda = lda[query_bow] # representation of the input (q_bow) in the latent space
    print('query_lda = ', query_lda)
    #query_norm = np.linalg.norm(query_lsi)
    #lsi.print_topics(20)
    
    # cosine similarity
    # ind_lda = similarities.MatrixSimilarity(lda[doc]) # transform corpus to LSI space and index it
    # sims_lda = ind_lda[query_lda] # calculate query-against-corpus cosine similarity 
    # print('sims_lda = ',sims_lda)
    
    # KL-divergence
    # KL_div = [prob_distr(lda[doc_repr], lda[query_lda], number_of_topics, "KL_divergence") for doc_repr in doc]
    # np_KL_div = np.asarray(KL_div)
    # print('KL_divergence = ',np_KL_div)
    
    # Hellinger distance
    hellinger = [prob_distr(lda[doc_repr], lda[query_lda], number_of_topics, "hellinger_distance") for doc_repr in doc]
    np_hellinger = np.asarray(hellinger)
    print('Hellinger distance = ',np_hellinger)
  
    print('{:.1f}s: Similarity matrix calculated'.format(time.time() - start_time))
    
    #sort similarity scores
    #sorted_sims = [(ext_doc[i], sim_score) for i, sim_score in enumerate(sims_lsi)]
    #print('sorted_sims:\t',sorted_sims)
    #corpus_sorted = tuple(sorted(sorted_sims, key=lambda sims_lsi: sims_lsi[1], reverse=True))
    #print('corpus_sorted:\t',corpus_sorted)
    #for i, (ext, score) in enumerate(corpus_sorted):
        #print('{} Q0 {} {} {} lsi_cos'.format(query_id,ext,(i+1),score))
    #    lsi_file.write('{} Q0 {} {} {} lsi_cos\n'.format(query_id,ext,(i+1),score))
    #break

lda_file.close()
tfidf_file.close()

51: Airbus Subsidies
query =  Airbus Subsidies
query_bow =  [(3066, 1), (5872, 1)]
query_lda =  [(0, 0.033333335), (1, 0.033333335), (2, 0.36666667), (3, 0.033333335), (4, 0.033333782), (5, 0.033333335), (6, 0.36666584), (7, 0.033333723), (8, 0.033333335), (9, 0.033333335)]
Hellinger distance =  [0.57252342 0.5689524  0.56173366 0.43552425 0.49028194 0.50913541
 0.55720844 0.52018896 0.52966488 0.52045289 0.67173904 0.75708283
 0.65228182 0.62970106 0.54341327 0.67373541 0.60891512 0.42523447
 0.45175095 0.81624554 0.55002484 0.72766205 0.72777762 0.54906782
 0.65197554 0.63459983 0.39576839 0.50088731 0.60902521 0.72449168
 0.75033832 0.71105527 0.72512195 0.69649286 0.42331983 0.37679746
 0.63296255 0.44420667 0.3846114  0.74546876 0.68194954 0.64115986
 0.66009176 0.59591395 0.61758481 0.58345825 0.58127682 0.71503089
 0.63053013 0.50588761 0.43367674 0.45526621 0.54611935 0.48309299
 0.53953803 0.59118925 0.81095156 0.72995889 0.72000043 0.68075324
 0.65095782 0.50812106 0.72636258

query =  South African Sanctions
query_bow =  [(54, 1), (846, 1), (2208, 1)]
query_lda =  [(0, 0.025000274), (1, 0.025002891), (2, 0.025000004), (3, 0.025000298), (4, 0.025000721), (5, 0.025003046), (6, 0.025000138), (7, 0.7749917), (8, 0.025000222), (9, 0.025000757)]
Hellinger distance =  [0.5419791  0.73441566 0.46057659 0.62003915 0.6937437  0.76601762
 0.74842064 0.52768326 0.68283462 0.76935574 0.65369813 0.50666084
 0.72979148 0.5885372  0.74178605 0.76205624 0.70680872 0.49749116
 0.62066182 0.59784491 0.66859973 0.75218949 0.58484236 0.7498597
 0.57326213 0.75102658 0.71058356 0.73760045 0.63028437 0.73587782
 0.70734145 0.67501819 0.58054249 0.72564027 0.66468396 0.63370252
 0.75835895 0.68926189 0.69783119 0.68590582 0.79628732 0.57839347
 0.80880426 0.81538625 0.7383032  0.69711161 0.68430441 0.79914496
 0.75149281 0.74359128 0.7967372  0.62651497 0.72057219 0.61647757
 0.80133946 0.82798799 0.79162832 0.7362225  0.62172696 0.49074817
 0.80151867 0.72804862 0.82354217 0.8129

query =  Leveraged Buyouts
query_bow =  [(4886, 1), (48553, 1)]
query_lda =  [(0, 0.03333333), (1, 0.03333333), (2, 0.36312264), (3, 0.03333333), (4, 0.37020296), (5, 0.03333333), (6, 0.033333465), (7, 0.03333333), (8, 0.03333333), (9, 0.03334094)]
Hellinger distance =  [0.57436208 0.45838605 0.53340744 0.36048347 0.36048195 0.44891329
 0.4552327  0.53569736 0.50995031 0.51572287 0.63521045 0.49559253
 0.53026918 0.60324481 0.51224508 0.3366925  0.3695163  0.61013734
 0.59580968 0.41626727 0.53805211 0.51606464 0.52073076 0.65202865
 0.45057034 0.66452923 0.54870105 0.6157899  0.56966671 0.53407643
 0.5707761  0.47141452 0.7811298  0.45711928 0.52453435 0.60893054
 0.63267621 0.45652025 0.66103897 0.43633397 0.35581014 0.50617269
 0.46704267 0.58232332 0.52061815 0.39411455 0.38150248 0.45121463
 0.63388856 0.52941133 0.65577377 0.65972057 0.5444422  0.56925696
 0.4985871  0.39323199 0.42133893 0.75464261 0.70331837 0.55385983
 0.65968391 0.41339977 0.51717146 0.58171531 0.5816467  0.4

query =  Satellite Launch Contracts
query_bow =  [(1339, 1), (1490, 1), (2231, 1)]
query_lda =  [(0, 0.025000123), (1, 0.025000118), (2, 0.025003126), (3, 0.025), (4, 0.27841607), (5, 0.025000129), (6, 0.025009084), (7, 0.025000192), (8, 0.5215709), (9, 0.025000293)]
Hellinger distance =  [0.55114359 0.52943497 0.5955015  0.65328778 0.6569557  0.74572088
 0.70661358 0.71753855 0.45208611 0.48347948 0.72400295 0.55785012
 0.58873108 0.51538165 0.53254731 0.68587864 0.58323475 0.58525822
 0.3785208  0.47854889 0.6944347  0.48392426 0.64804539 0.64232261
 0.47348549 0.76535044 0.4268704  0.70291351 0.58034883 0.64489803
 0.57344172 0.57943428 0.44019977 0.74944818 0.72705109 0.65392462
 0.65715653 0.52922415 0.65750361 0.75955963 0.59085001 0.60505253
 0.45291016 0.59111811 0.53702094 0.75118193 0.63628124 0.42171214
 0.51761249 0.76366971 0.64431029 0.53830208 0.35533317 0.73767463
 0.58275322 0.54832266 0.5463394  0.75168904 0.61586657 0.77514966
 0.51256464 0.70765241 0.65656314 0.6641

query =  Insider Trading
query_bow =  [(235, 1), (4400, 1)]
query_lda =  [(0, 0.033333335), (1, 0.033333573), (2, 0.4169902), (3, 0.033333335), (4, 0.31634212), (5, 0.033333335), (6, 0.03333411), (7, 0.033333343), (8, 0.033333335), (9, 0.033333365)]
Hellinger distance =  [0.67489997 0.63712565 0.63637497 0.62310196 0.64494633 0.73169567
 0.75019443 0.81375432 0.52540459 0.74062221 0.76903862 0.80836745
 0.70666723 0.77778755 0.74083269 0.7789149  0.77929287 0.78787211
 0.64131113 0.67270265 0.66394904 0.75130357 0.65033451 0.77085928
 0.80496687 0.70123809 0.77807997 0.74486791 0.77503578 0.7226196
 0.8139965  0.71151939 0.78249586 0.75437161 0.81620424 0.73011323
 0.71225974 0.65565699 0.77087488 0.73398374 0.65427524 0.72854891
 0.80773044 0.81627336 0.69014124 0.70219722 0.78206799 0.74178799
 0.59707957 0.722362   0.77655948 0.7225187  0.64172113 0.73178081
 0.78528708 0.72047492 0.69365106 0.4715558  0.73285859 0.72697354
 0.76798849 0.62473334 0.74854455 0.74971379 0.73284274 0.7

...

71: Border Incursions
query =  Border Incursions
query_bow =  [(580, 1), (120650, 1)]
query_lda =  [(0, 0.033333335), (1, 0.033335965), (2, 0.03333333), (3, 0.033334617), (4, 0.03333333), (5, 0.03333364), (6, 0.03333333), (7, 0.69998884), (8, 0.03333333), (9, 0.03334022)]
Hellinger distance =  [0.67385085 0.68806188 0.78097343 0.73933639 0.79631311 0.83555891
 0.78219459 0.75512342 0.77099963 0.7509626  0.71009348 0.74510748
 0.81020952 0.73171928 0.72954576 0.75395435 0.8441073  0.78285023
 0.81297545 0.7256814  0.77340192 0.68742096 0.84715503 0.71503418
 0.58778277 0.83387253 0.7577796  0.76009237 0.71265128 0.77326671
 0.58073005 0.80906169 0.57360533 0.74041063 0.37517847 0.42836565
 0.73532604 0.68138338 0.82454333 0.74137276 0.83027024 0.78337344
 0.86193525 0.85680775 0.78022044 0.77546855 0.75680129 0.7284067
 0.7659684  0.69631184 0.82892264 0.7877718  0.42971009 0.70718686
 0.78461812 0.55703993 0.69089331 0.72764401 0.53723277 0.50272428
 0.75983611 0.81518192 0.62600124 0.

query =  Demographic Shifts in the U.S.
query_bow =  [(71970, 1), (218232, 1)]
query_lda =  [(0, 0.033335045), (1, 0.033333823), (2, 0.033333976), (3, 0.03333872), (4, 0.033335354), (5, 0.033334877), (6, 0.6999776), (7, 0.03333588), (8, 0.03334138), (9, 0.03333333)]
Hellinger distance =  [0.4847347  0.7908449  0.79211613 0.79313162 0.83972943 0.56701399
 0.59056619 0.75354494 0.48967073 0.68178327 0.71305648 0.84756992
 0.43285968 0.35847956 0.77116805 0.58303948 0.77761247 0.76016831
 0.6655647  0.49253203 0.52919629 0.47252943 0.36115862 0.7338208
 0.51866274 0.55126577 0.46330796 0.79326792 0.48666047 0.65686989
 0.60114404 0.56864254 0.52461291 0.58864472 0.62196412 0.58672139
 0.68295318 0.4139875  0.82991334 0.43094499 0.60620752 0.77221119
 0.71502794 0.50368363 0.3957332  0.58024987 0.76230634 0.81205707
 0.77280327 0.65758284 0.72892418 0.70795385 0.46960398 0.72397117
 0.71033262 0.67102293 0.54859847 0.4186516  0.37959846 0.34811137
 0.42245658 0.57069534 0.53539306 0.414995

73: Demographic Shifts across National Boundaries
query =  Demographic Shifts across National Boundaries
query_bow =  [(21, 1), (43984, 1), (71970, 1), (218232, 1)]
query_lda =  [(0, 0.020001113), (1, 0.020005092), (2, 0.02000038), (3, 0.02000261), (4, 0.020002915), (5, 0.020002851), (6, 0.02000574), (7, 0.020005835), (8, 0.81997347), (9, 0.02000003)]
Hellinger distance =  [0.35613278 0.80131519 0.4613322  0.51271329 0.65569896 0.68648943
 0.65094484 0.39011321 0.74300924 0.76606609 0.45452746 0.50672229
 0.60780594 0.72230679 0.63268105 0.69639086 0.53527838 0.60212172
 0.76418112 0.72309241 0.45008514 0.55752719 0.71215378 0.67007955
 0.66657091 0.47470446 0.74689737 0.65266654 0.42020067 0.54677123
 0.69156395 0.76599006 0.81786086 0.70656625 0.71696586 0.70830957
 0.62040696 0.6996054  0.66514706 0.73423376 0.55926638 0.56912634
 0.71740149 0.53232186 0.63340231 0.57552065 0.7739242  0.47975846
 0.50516075 0.71859399 0.80267653 0.61799987 0.71500173 0.685018
 0.47218396 0.76516769 

query =  Conflicting Policy
query_bow =  [(238, 1), (61863, 1)]
query_lda =  [(0, 0.03333371), (1, 0.033333365), (2, 0.033339206), (3, 0.033344414), (4, 0.033352558), (5, 0.6999162), (6, 0.033341926), (7, 0.033347875), (8, 0.033336475), (9, 0.03335432)]


KeyboardInterrupt: 

In [63]:
import matplotlib.pyplot as plt
from subprocess import Popen, PIPE
from collections import defaultdict

def extract_needed_metric(filename, metric):
    metric_scores = defaultdict(float)
    eval_file = open(filename, "r")
    for line in eval_file:
        cur_line = line.split()
        if cur_line[0] == metric and cur_line[1] != 'all':
            metric_scores[int(cur_line[1])] = float(cur_line[2])
    eval_file.close()
    return metric_scores

def t_test(data):
    pass

def task2_evaluation(model_name):
    
    file_name = model_name + '.run'
    #ev_methods = '('+ eval_metric +'\W+all)'
    qrel_set = 'ap_88_89/qrel_validation'
    wd = '/home/hw2/Downloads/'
    #cmd = wd + 'trec_eval/trec_eval -m all_trec -q "'+ wd + qrel_set + '" "'+ wd + file_name + '" | grep -E "' + ev_methods + '" > ' + model_name + eval_metric + '.eval'
    
    #obtain all measures
    cmd = wd + 'trec_eval/trec_eval -m all_trec -q "'+ wd + qrel_set + '" "'+ wd + file_name + '" > '+ wd + model_name + '.eval'
    print(cmd)
    pipe = Popen(cmd, stdin=PIPE)
    print(pipe.write())
    #ndcg = float(subprocess.check_output(cmd, shell=True).decode('utf-8').split('\t')[2].strip())
    #return ndcg
    """
    plt.title(model_name + ' hyper parameter values')
    plt.plot(params, ndcgs)
    plt.xlabel('hyper parameter value')
    plt.ylabel('ndcg')
    plt.show()
    """

#metrics = ['ndcg_cut_10','recall_1000','map_cut_1000','precision_cut_5']
#for metric in metrics:
#ev_metric_score = task2_evaluation('lsi10topics')
#ev_metric_score = task2_evaluation('lsi200topics')
#print('LSI results: '+metric+' '+ev_metric_score)
ndcg_cut_10 = extract_needed_metric('lsi200topics.eval', 'ndcg_cut_10')
recall_1000 = extract_needed_metric('lsi200topics.eval', 'recall_1000')
map_cut_1000 = extract_needed_metric('lsi200topics.eval', 'recall_1000')
precision_5 = extract_needed_metric('lsi200topics.eval', 'P_5')

list_ndcg_cut_10 = list(ndcg_cut_10.values())
print('NDCG @ 10: ',list_ndcg_cut_10,'\n')

list_recall_1000 = list(recall_1000.values())
print('Recall @ 1000: ',list_recall_1000,'\n')

list_map_cut_1000 = list(map_cut_1000.values())
print('MAP @ 1000',list_map_cut_1000,'\n')

list_precision_5 = list(precision_5.values())
print('Precision @ 5: ',list_precision_5,'\n')

# t-tests for LSI vs. LDA for each metric

NDCG @ 10:  [0.0, 0.4521, 0.2426, 0.0, 0.0, 0.5366, 0.0, 0.2369, 0.1585, 0.0, 0.0, 0.0, 0.0, 0.0, 0.7827, 0.0, 0.0, 0.0948, 0.6236, 0.2025, 0.0, 0.0, 0.8701, 0.0, 0.0, 0.11, 0.0663, 0.0, 0.0, 0.0] 

Recall @ 1000:  [0.6909, 0.8571, 0.8293, 0.35, 0.2857, 0.8133, 0.4317, 0.5238, 0.65, 0.1111, 0.2, 0.92, 0.7, 1.0, 0.9212, 0.6357, 0.5962, 0.9777, 0.8333, 1.0, 1.0, 0.1081, 1.0, 1.0, 0.5263, 1.0, 0.2391, 0.9463, 0.6571, 0.3333] 

MAP @ 1000 [0.6909, 0.8571, 0.8293, 0.35, 0.2857, 0.8133, 0.4317, 0.5238, 0.65, 0.1111, 0.2, 0.92, 0.7, 1.0, 0.9212, 0.6357, 0.5962, 0.9777, 0.8333, 1.0, 1.0, 0.1081, 1.0, 1.0, 0.5263, 1.0, 0.2391, 0.9463, 0.6571, 0.3333] 

Precision @ 5:  [0.0, 0.4, 0.2, 0.0, 0.0, 0.4, 0.0, 0.2, 0.2, 0.0, 0.0, 0.0, 0.0, 0.0, 0.8, 0.0, 0.0, 0.2, 0.6, 0.2, 0.0, 0.0, 1.0, 0.0, 0.0, 0.2, 0.0, 0.0, 0.0, 0.0] 



### Task 3:  Word embeddings for ranking [20 points] (open-ended) ###

First create word embeddings on the corpus we provided using [word2vec](http://arxiv.org/abs/1411.2738) -- [gensim implementation](https://radimrehurek.com/gensim/models/word2vec.html). You should extract the indexed documents using pyndri and provide them to gensim for training a model (see example [here](https://github.com/nickvosk/pyndri/blob/master/examples/word2vec.py)).
   
This is an open-ended task. It is left up you to decide how you will combine word embeddings to derive query and document representations. Note that since we provide the implementation for training word2vec, you will be graded based on your creativity on combining word embeddings for building query and document representations.

Note: If you want to experiment with pre-trained word embeddings on a different corpus, you can use the word embeddings we provide alongside the assignment (./data/reduced_vectors_google.txt.tar.gz). These are the [google word2vec word embeddings](https://code.google.com/archive/p/word2vec/), reduced to only the words that appear in the document collection we use in this assignment.

In [ ]:
import copy
import pyndri
import pyndri.compat
import sys
import time
from gensim import corpora, models, similarities


start_time = time.time()
print('{:.1f}s: Loading pyndri index'.format(time.time() - start_time))
index = pyndri.Index('index/')
dictionary = pyndri.extract_dictionary(index)

print('{:.1f}s: Converting to IndriSentences'.format(time.time() - start_time))
sentences = pyndri.compat.IndriSentences(index, dictionary)

print('{:.1f}s: Test IndriSentences'.format(time.time() - start_time))
for i, doc in enumerate(sentences):
    if i>=3:
        break
    print(doc)

print('{:.1f}s: Building vocab'.format(time.time() - start_time))
word2vec_init = gensim.models.Word2Vec(
    size=300,  # Embedding size
    window=5,  # One-sided window size
    sg=True,  # Skip-gram.
    min_count=5,  # Minimum word frequency.
    sample=1e-3,  # Sub-sample threshold.
    hs=False,  # Hierarchical softmax.
    negative=10,  # Number of negative examples.
    iter=1,  # Number of iterations.
    workers=8,  # Number of workers.
)
word2vec_init.build_vocab(sentences, trim_rule=None)

print('{:.1f}s: Training word2vec'.format(time.time() - start_time))
models = [word2vec_init]
for epoch in range(1, 5 + 1):
    print('{:.1f}s: start epoch {}'.format(time.time() - start_time, epoch))
    model = copy.deepcopy(models[-1])
    model.train(sentences)
    models.append(model)
    


print('{:.1f}s: Loading queries'.format(time.time() - start_time))

with open('./ap_88_89/topics_title', 'r') as f_topics:
    queries = parse_topics([f_topics])

tokenized_queries = {
    query_id: [dictionary.translate_token(token)
               for token in index.tokenize(query_string)
               if dictionary.has_token(token)]
    for query_id, query_string in queries.items()}

query_term_ids = set(
    query_term_id
    for query_term_ids in tokenized_queries.values()
    for query_term_id in query_term_ids)

### Task 4: Learning to rank (LTR) [15 points] (open-ended) ###

In this task you will get an introduction into learning to rank for information retrieval.

You can explore different ways for devising features for the model. Obviously, you can use the retrieval methods you implemented in Task 1, Task 2 and Task 3 as features. Think about other features you can use (e.g. query/document length). Creativity on devising new features and providing motivation for them will be taken into account when grading.

For every query, first create a document candidate set using the top-1000 documents using TF-IDF, and subsequently compute features given a query and a document. Note that the feature values of different retrieval methods are likely to be distributed differently.

You are adviced to start some pointwise learning to rank algorithm e.g. logistic regression, implemented in [scikit-learn](http://scikit-learn.org/stable/modules/generated/sklearn.linear_model.LogisticRegression.html).
Train your LTR model using 10-fold cross validation on the test set. More advanced learning to rank algorithms will be appreciated when grading.

### Task 5: Write a report [15 points; instant FAIL if not provided] ###

The report should be a PDF file created using the [sigconf ACM template](https://www.acm.org/publications/proceedings-template) and will determine a significant part of your grade.

   * It should explain what you have implemented, motivate your experiments and detail what you expect to learn from them. **[10 points]**
   * Lastly, provide a convincing analysis of your results and conclude the report accordingly. **[10 points]**
      * Do all methods perform similarly on all queries? Why?
      * Is there a single retrieval model that outperforms all other retrieval models (i.e., silver bullet)?
      * ...

**Hand in the report and your self-contained implementation source files.** Only send us the files that matter, organized in a well-documented zip/tgz file with clear instructions on how to reproduce your results. That is, we want to be able to regenerate all your results with minimal effort. You can assume that the index and ground-truth information is present in the same file structure as the one we have provided.
